In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 20000 
args.init_model = "{}-attention-random-sink1-test1".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 4001
args.conn_lambda_epochs_end = 12000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 4001
args.valency_lambda_epochs_end = 12000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 4001
args.euler_lambda_epochs_end = 12000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 12000

args.cross_att_use = True
args.cross_att_random = True
args.cross_att_n_sinkhorn = 1
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=12000, conn_lambda_epochs_start=4001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=1, cross_att_random=True, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=12000, euler_lambda_epochs_start=4001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='deepsets-attention-random-sink1-test1_decode', init_model='deepsets-attention-random-sink1-test1', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=20000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_o

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

No model deepsets-attention-random-sink1-test1 found in mol_opt/output_dev4/deepsets-attention-random-sink1-test1! Starting from scratch.
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=-1 mode=[0 0 0] conn=True val=True euler=True
Epoch: 1


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:12471.9050000
 conn_penalty:0.0000000
 val_penalty:654.5385156
 euler_penalty:195.7443750
 total:12472.7537500
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 1, train
 fgw:12471.9050000
 conn_penalty:0.0000000
 val_penalty:654.5385156
 euler_penalty:195.7443750
 total:12472.7537500
Epoch duration: 3.083644151687622
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_1
Epoch: 2
Losses Batch 0, train
 fgw:2982427303608.3198242
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:2982427303608.3198242
Penalty params: tau=0.99962 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=2 mode=[0 0 0] conn=False val=False euler=False
Pen

Losses Batch 0, train
 fgw:61983646.7200000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:61983646.7200000
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 13, train
 fgw:61983646.7200000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:61983646.7200000
Epoch duration: 0.6524868011474609
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_13
Epoch: 14
Losses Batch 0, train
 fgw:76122777.6000000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:76122777.6000000
Penalty params: tau=0.99502 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=14 mode=[0 0 0] conn=False val=False euler=False
Pe

Losses Batch 0, train
 fgw:189366456.3200000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:189366456.3200000
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 25, train
 fgw:189366456.3200000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:189366456.3200000
Epoch duration: 0.7090463638305664
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_25
Epoch: 26
Losses Batch 0, train
 fgw:153894133.7600000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:153894133.7600000
Penalty params: tau=0.99045 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=26 mode=[0 0 0] conn=False val=False euler=Fa

...

Losses Batch 0, train
 fgw:430529618903.0399780
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:430529618903.0399780
Penalty params: tau=0.06059 conn_l=0.02734 val_l=0.03377 euler_l=0.02312 epoch=7306 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06059 conn_l=0.02734 val_l=0.03377 euler_l=0.02312 epoch=7306 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7306, train
 fgw:430529618903.0399780
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:430529618903.0399780
Epoch duration: 4.580368518829346
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_7306
Epoch: 7307
Losses Batch 0, train
 fgw:246276906024.9599915
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:246276906024.9599915
Penalty params: tau=0.06057 conn_l=0.02737 val_l=0.03381 euler_l=0.02315 epoch=7307 mode=[1

Losses Batch 0, train
 fgw:341496226119.6799927
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:341496226119.6799927
Penalty params: tau=0.06033 conn_l=0.02765 val_l=0.03417 euler_l=0.02337 epoch=7317 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06033 conn_l=0.02765 val_l=0.03417 euler_l=0.02337 epoch=7317 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7317, train
 fgw:341496226119.6799927
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:341496226119.6799927
Epoch duration: 4.54708456993103
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_7317
Epoch: 7318
Losses Batch 0, train
 fgw:424905392783.3599854
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:424905392783.3599854
Penalty params: tau=0.06031 conn_l=0.02767 val_l=0.03420 euler_l=0.02339 epoch=7318 mode=[1 

Losses Batch 0, train
 fgw:139363342090.2399902
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:139363342090.2399902
Penalty params: tau=0.06008 conn_l=0.02795 val_l=0.03457 euler_l=0.02361 epoch=7328 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06008 conn_l=0.02795 val_l=0.03457 euler_l=0.02361 epoch=7328 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7328, train
 fgw:139363342090.2399902
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:139363342090.2399902
Epoch duration: 4.776214838027954
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_7328
Epoch: 7329
Losses Batch 0, train
 fgw:95716041031.6799927
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:95716041031.6799927
Penalty params: tau=0.06006 conn_l=0.02798 val_l=0.03461 euler_l=0.02364 epoch=7329 mode=[1 1

Losses Batch 0, train
 fgw:98028077711.3600006
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:98028077711.3600006
Penalty params: tau=0.05983 conn_l=0.02826 val_l=0.03498 euler_l=0.02386 epoch=7339 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.05983 conn_l=0.02826 val_l=0.03498 euler_l=0.02386 epoch=7339 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7339, train
 fgw:98028077711.3600006
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:98028077711.3600006
Epoch duration: 4.493187427520752
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink1-test1/model_deepsets-attention-random-sink1-test1_7339
Epoch: 7340
Losses Batch 0, train
 fgw:103559913799.6799927
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:103559913799.6799927
Penalty params: tau=0.05980 conn_l=0.02829 val_l=0.03501 euler_l=0.02388 epoch=7340 mode=[1 1 1

KeyboardInterrupt: 